# Data Analysis

In [1]:
import numpy as np
import xarray as xr
import hvplot.xarray
import holoviews as hv

from conflict_monitoring_ntl.case_studies import get_county_ids, get_date
from conflict_monitoring_ntl.layers import get_rasters_for_admin

hv.output(widget_location='bottom')

In [2]:
import warnings
warnings.filterwarnings('ignore',
    message='Connection pool is full, discarding connection*',
    module='urllib3.connectionpool'
)

In [3]:
import logging
logging.getLogger("pyogrio._io").setLevel(logging.WARNING)

In [4]:
SDGSAT_THRESHOLDS = np.arange(1.0, 4.0, 0.25).tolist()
BM_THRESHOLDS = np.arange(0.5, 3.0, 0.25).tolist()

**Radiance Conversion and Band Scaling**

- **L** denotes the radiance intensity at the entrance pupil of the sensor.
- **L** is measured in units of **W/m²/sr/µm** (watts per square meter per steradian per micrometer).
- **DN** represents the original digital number (pixel value) of the image.
- **Gain** is the amplification factor; **Bias** is the offset for radiometric calibration.

**Radiance Calculation**

$$
L = DN \times \text{Gain} + \text{Bias}
$$

**Conversion to `nW/cm²/sr`**

To convert GLI band radiance to the brightness unit `nW/cm²/sr`(same as Black Marble), multiply by the bandwidth (in microns) and a SI scaling factor.

- Bandwidth: $0.466\,\mu\text{m}$.

$$
\text{Radiance}_{(\text{nW}/\text{cm}^2/\text{sr})} = L_{(\text{W}/\text{m}^2/\text{sr}/\mu\text{m})} \times 10^5 \times \text{bandwidth}_{\mu\text{m}}
$$

## Sudan

In [5]:
country = "Sudan"
date, county_ids = get_date(country), get_county_ids(country)

xds = get_rasters_for_admin(
    county_ids[0], 
    date,
    sdgsat_dn="PH",
    sdgsat_binary_thresholds=SDGSAT_THRESHOLDS,
    bm_binary_thresholds=BM_THRESHOLDS
)

In [6]:
def plot_radiance_comparison(xds: xr.Dataset):
    """Helper function for plotting SDGSat and Black Marble side by side."""
    sdgsat_plot = xds["sdgsat_radiance"].hvplot.image(
        x="lon", 
        y="lat", 
        geo=True,
        crs=xds.rio.crs,
        cmap='inferno',
        width=400,
        height=400,
        clim=(7, 7.5),
        title="SDGSat resampled (nW/cm²/sr)",
    )

    bm_plot = xds["black_marble_radiance"].hvplot.image(
        x="lon", 
        y="lat", 
        geo=True,
        crs=xds.rio.crs,
        cmap='inferno',
        width=400,
        height=400,
        clim=(0, 2),
        title="Black Marble (nW/cm²/sr)"
    )

    return sdgsat_plot + bm_plot

plot_radiance_comparison(xds)

:Layout
   .Image.I  :Image   [lon,lat]   (sdgsat_radiance)
   .Image.II :Image   [lon,lat]   (black_marble_radiance)

In [7]:
def plot_binary(xds: xr.Dataset, satellite: str, threshold: float):
    """Helper function for plotting binarized tiles."""
    threshold_str = str(threshold).replace(".", "_")
    satellite_str = satellite.lower().replace(" ", "_")

    return xds[f"{satellite_str}_binary_{threshold_str}"].hvplot.image(
        x="lon", 
        y="lat", 
        geo=True,
        crs=xds.rio.crs,
        cmap='inferno',
        width=500,
        height=400,
        clim=(0, 1),
        title=f"{satellite} Binarized",
        colorbar=False
    )

In [8]:
curve_dict_sdgsat = {t: plot_binary(xds, "SDGSat", t) for t in SDGSAT_THRESHOLDS}
hv.HoloMap(curve_dict_sdgsat, kdims='threshold')

:HoloMap   [threshold]
   :Image   [lon,lat]   (sdgsat_binary_3_75)

In [9]:
curve_dict_bm = {t: plot_binary(xds, "Black Marble", t) for t in BM_THRESHOLDS}
hv.HoloMap(curve_dict_bm, kdims='threshold')

:HoloMap   [threshold]
   :Image   [lon,lat]   (black_marble_binary_2_75)

## Mali

In [10]:
country = "Mali"
date, county_ids = get_date(country), get_county_ids(country)

xds = get_rasters_for_admin(
    county_ids[0], 
    date,
    sdgsat_dn="PH",
    sdgsat_binary_thresholds=SDGSAT_THRESHOLDS,
    bm_binary_thresholds=BM_THRESHOLDS
)

In [11]:
plot_radiance_comparison(xds)

:Layout
   .Image.I  :Image   [lon,lat]   (sdgsat_radiance)
   .Image.II :Image   [lon,lat]   (black_marble_radiance)

In [12]:
curve_dict_sdgsat = {t: plot_binary(xds, "SDGSat", t) for t in SDGSAT_THRESHOLDS}
hv.HoloMap(curve_dict_sdgsat, kdims='threshold')

:HoloMap   [threshold]
   :Image   [lon,lat]   (sdgsat_binary_3_75)

In [13]:
curve_dict_bm = {t: plot_binary(xds, "Black Marble", t) for t in BM_THRESHOLDS}
hv.HoloMap(curve_dict_bm, kdims='threshold')

:HoloMap   [threshold]
   :Image   [lon,lat]   (black_marble_binary_2_75)

## Syria

In [14]:
country = "Syria"
date, county_ids = get_date(country), get_county_ids(country)

xds = get_rasters_for_admin(
    county_ids[0], 
    date,
    sdgsat_dn="PH",
    sdgsat_binary_thresholds=SDGSAT_THRESHOLDS,
    bm_binary_thresholds=BM_THRESHOLDS
)

In [15]:
plot_radiance_comparison(xds)

:Layout
   .Image.I  :Image   [lon,lat]   (sdgsat_radiance)
   .Image.II :Image   [lon,lat]   (black_marble_radiance)

In [16]:
curve_dict_sdgsat = {t: plot_binary(xds, "SDGSat", t) for t in SDGSAT_THRESHOLDS}
hv.HoloMap(curve_dict_sdgsat, kdims='threshold')

:HoloMap   [threshold]
   :Image   [lon,lat]   (sdgsat_binary_3_75)

In [17]:
curve_dict_bm = {t: plot_binary(xds, "Black Marble", t) for t in BM_THRESHOLDS}
hv.HoloMap(curve_dict_bm, kdims='threshold')

:HoloMap   [threshold]
   :Image   [lon,lat]   (black_marble_binary_2_75)

## Central African Republic

In [18]:
country = "Central African Republic"
date, county_ids = get_date(country), get_county_ids(country)

xds = get_rasters_for_admin(
    county_ids[0], 
    date,
    sdgsat_dn="PH",
    sdgsat_binary_thresholds=SDGSAT_THRESHOLDS,
    bm_binary_thresholds=BM_THRESHOLDS
)

In [19]:
plot_radiance_comparison(xds)

:Layout
   .Image.I  :Image   [lon,lat]   (sdgsat_radiance)
   .Image.II :Image   [lon,lat]   (black_marble_radiance)

In [20]:
curve_dict_sdgsat = {t: plot_binary(xds, "SDGSat", t) for t in SDGSAT_THRESHOLDS}
hv.HoloMap(curve_dict_sdgsat, kdims='threshold')

:HoloMap   [threshold]
   :Image   [lon,lat]   (sdgsat_binary_3_75)

In [21]:
curve_dict_bm = {t: plot_binary(xds, "Black Marble", t) for t in BM_THRESHOLDS}
hv.HoloMap(curve_dict_bm, kdims='threshold')

:HoloMap   [threshold]
   :Image   [lon,lat]   (black_marble_binary_2_75)

## Democratic Republic of the Congo

In [22]:
country = "Democratic Republic of the Congo"
date, county_ids = get_date(country), get_county_ids(country)

xds = get_rasters_for_admin(
    county_ids[5], 
    date,
    sdgsat_dn="PH",
    sdgsat_binary_thresholds=SDGSAT_THRESHOLDS,
    bm_binary_thresholds=BM_THRESHOLDS
)

In [23]:
plot_radiance_comparison(xds)

:Layout
   .Image.I  :Image   [lon,lat]   (sdgsat_radiance)
   .Image.II :Image   [lon,lat]   (black_marble_radiance)

In [24]:
curve_dict_sdgsat = {t: plot_binary(xds, "SDGSat", t) for t in SDGSAT_THRESHOLDS}
hv.HoloMap(curve_dict_sdgsat, kdims='threshold')

:HoloMap   [threshold]
   :Image   [lon,lat]   (sdgsat_binary_3_75)

In [25]:
curve_dict_bm = {t: plot_binary(xds, "Black Marble", t) for t in BM_THRESHOLDS}
hv.HoloMap(curve_dict_bm, kdims='threshold')

:HoloMap   [threshold]
   :Image   [lon,lat]   (black_marble_binary_2_75)

## Ethiopia

In [26]:
country = "Ethiopia"
date, county_ids = get_date(country), get_county_ids(country)

xds = get_rasters_for_admin(
    county_ids[2], 
    date,
    sdgsat_dn="PH",
    sdgsat_binary_thresholds=SDGSAT_THRESHOLDS,
    bm_binary_thresholds=BM_THRESHOLDS
)

In [27]:
plot_radiance_comparison(xds)

:Layout
   .Image.I  :Image   [lon,lat]   (sdgsat_radiance)
   .Image.II :Image   [lon,lat]   (black_marble_radiance)

In [28]:
curve_dict_sdgsat = {t: plot_binary(xds, "SDGSat", t) for t in SDGSAT_THRESHOLDS}
hv.HoloMap(curve_dict_sdgsat, kdims='threshold')

:HoloMap   [threshold]
   :Image   [lon,lat]   (sdgsat_binary_3_75)

In [29]:
curve_dict_bm = {t: plot_binary(xds, "Black Marble", t) for t in BM_THRESHOLDS}
hv.HoloMap(curve_dict_bm, kdims='threshold')

:HoloMap   [threshold]
   :Image   [lon,lat]   (black_marble_binary_2_75)

## Myanmar

In [30]:
country = "Myanmar"
date, county_ids = get_date(country), get_county_ids(country)

xds = get_rasters_for_admin(
    county_ids[0], 
    date,
    sdgsat_dn="PH",
    sdgsat_binary_thresholds=SDGSAT_THRESHOLDS,
    bm_binary_thresholds=BM_THRESHOLDS
)

In [31]:
plot_radiance_comparison(xds)

:Layout
   .Image.I  :Image   [lon,lat]   (sdgsat_radiance)
   .Image.II :Image   [lon,lat]   (black_marble_radiance)

In [32]:
curve_dict_sdgsat = {t: plot_binary(xds, "SDGSat", t) for t in SDGSAT_THRESHOLDS}
hv.HoloMap(curve_dict_sdgsat, kdims='threshold')

:HoloMap   [threshold]
   :Image   [lon,lat]   (sdgsat_binary_3_75)

In [33]:
curve_dict_bm = {t: plot_binary(xds, "Black Marble", t) for t in BM_THRESHOLDS}
hv.HoloMap(curve_dict_bm, kdims='threshold')

:HoloMap   [threshold]
   :Image   [lon,lat]   (black_marble_binary_2_75)

## Nigeria

In [34]:
country = "Nigeria"
date, county_ids = get_date(country), get_county_ids(country)

xds = get_rasters_for_admin(
    county_ids[0], 
    date,
    sdgsat_dn="PH",
    sdgsat_binary_thresholds=SDGSAT_THRESHOLDS,
    bm_binary_thresholds=BM_THRESHOLDS
)

In [35]:
plot_radiance_comparison(xds)

:Layout
   .Image.I  :Image   [lon,lat]   (sdgsat_radiance)
   .Image.II :Image   [lon,lat]   (black_marble_radiance)

In [36]:
curve_dict_sdgsat = {t: plot_binary(xds, "SDGSat", t) for t in SDGSAT_THRESHOLDS}
hv.HoloMap(curve_dict_sdgsat, kdims='threshold')

:HoloMap   [threshold]
   :Image   [lon,lat]   (sdgsat_binary_3_75)

In [37]:
curve_dict_bm = {t: plot_binary(xds, "Black Marble", t) for t in BM_THRESHOLDS}
hv.HoloMap(curve_dict_bm, kdims='threshold')

:HoloMap   [threshold]
   :Image   [lon,lat]   (black_marble_binary_2_75)

## South Sudan

In [38]:
country = "South Sudan"
date, county_ids = get_date(country), get_county_ids(country)

xds = get_rasters_for_admin(
    county_ids[0], 
    date,
    sdgsat_dn="PH",
    sdgsat_binary_thresholds=SDGSAT_THRESHOLDS,
    bm_binary_thresholds=BM_THRESHOLDS
)

In [39]:
plot_radiance_comparison(xds)

:Layout
   .Image.I  :Image   [lon,lat]   (sdgsat_radiance)
   .Image.II :Image   [lon,lat]   (black_marble_radiance)

In [40]:
curve_dict_sdgsat = {t: plot_binary(xds, "SDGSat", t) for t in SDGSAT_THRESHOLDS}
hv.HoloMap(curve_dict_sdgsat, kdims='threshold')

:HoloMap   [threshold]
   :Image   [lon,lat]   (sdgsat_binary_3_75)

In [41]:
curve_dict_bm = {t: plot_binary(xds, "Black Marble", t) for t in BM_THRESHOLDS}
hv.HoloMap(curve_dict_bm, kdims='threshold')

:HoloMap   [threshold]
   :Image   [lon,lat]   (black_marble_binary_2_75)